# Optunaの動作確認サンプル

ハイパーパラメータの自動チューニングができるライブラリ[Optuna](https://www.preferred.jp/ja/projects/optuna/)の動作確認を行う．  
機械学習モデルの開発において，精度向上の最後の一押しを効率化できる．

[GBDTの試行](https://qiita.com/DS27/items/aa3f6d0f03a8053e5810#6-gbdt%E5%8B%BE%E9%85%8D%E3%83%96%E3%83%BC%E3%82%B9%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%E6%9C%A8%E3%81%AB%E3%81%A4%E3%81%84%E3%81%A6)で高い精度が得られており，このモデルをハイパーパラメータチューニングのベースラインとする．

## データセットの読み込み(ボストン住宅価格)

In [1]:
from sklearn.datasets import load_boston
import pandas as pd

boston = load_boston()
df_x_boston = pd.DataFrame(boston['data'], columns=boston['feature_names'])
df_y_boston = pd.DataFrame(boston['target'], columns=['MEDV'])
df_boston = pd.concat([df_x_boston, df_y_boston], axis=1)

### 欠損値確認

In [2]:
df_boston.isnull().sum()

CRIM       0
ZN         0
INDUS      0
CHAS       0
NOX        0
RM         0
AGE        0
DIS        0
RAD        0
TAX        0
PTRATIO    0
B          0
LSTAT      0
MEDV       0
dtype: int64

### 学習データと評価データの分割

In [3]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(df_x_boston, df_y_boston, test_size=0.3, random_state=0)

### データの標準化

In [4]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
sc.fit(x_train)
x_train_std = sc.transform(x_train)
x_test_std = sc.transform(x_test)

## GBDTの学習と評価

In [5]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.metrics import r2_score
from sklearn.metrics import mean_absolute_error

gbr = GradientBoostingRegressor()
gbr.fit(x_train_std, y_train)

pred_gbr = gbr.predict(x_test_std)
r2_gbr = r2_score(y_test, pred_gbr)
mae_gbr = mean_absolute_error(y_test, pred_gbr)

print("R2 : %.3f" % r2_gbr)
print("MAE : %.3f" % mae_gbr)

R2 : 0.847
MAE : 2.431


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


### Optuna

GradientBoostingRegressorデフォルト値

```
class sklearn.ensemble.GradientBoostingRegressor(*, loss='squared_error', learning_rate=0.1, n_estimators=100, subsample=1.0, criterion='friedman_mse', min_samples_split=2, min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_depth=3, min_impurity_decrease=0.0, init=None, random_state=None, max_features=None, alpha=0.9, verbose=0, max_leaf_nodes=None, warm_start=False, validation_fraction=0.1, n_iter_no_change=None, tol=0.0001, ccp_alpha=0.0)
```


In [6]:
import optuna

In [7]:
def objective(trial):
    lr = trial.suggest_loguniform('learning_rate', 0.001, 0.1)
    n_estimators = trial.suggest_int('n_estimators', 10, 1000)
    min_samples_split = trial.suggest_int('min_samples_split', 2, 10)
    min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 10)
    max_depth = trial.suggest_int('max_depth', 1, 10)
    
    gbr = GradientBoostingRegressor(
        learning_rate=lr, 
        n_estimators=n_estimators, 
        min_samples_split=min_samples_split,
        min_samples_leaf=min_samples_leaf,
        max_depth=max_depth)
    gbr.fit(x_train_std, y_train)
    
    pred_gbr = gbr.predict(x_test_std)
    r2_gbr = r2_score(y_test, pred_gbr)

    return 1-r2_gbr

n_trials = 10000
study = optuna.create_study()
study.optimize(objective, n_trials=n_trials)

[I 2022-06-11 20:55:57,521] A new study created in memory with name: no-name-8eb7c351-990c-43f7-83f3-e30316ced68e
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:55:57,689] Trial 0 finished with value: 0.21267547409860543 and parameters: {'learning_rate': 0.019374255768878353, 'n_estimators': 223, 'min_samples_split': 9, 'min_samples_leaf': 7, 'max_depth': 4}. Best is trial 0 with value: 0.21267547409860543.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:55:57,759] Trial 1 finished with value: 0.21190116352079247 and parameters: {'learning_rate'

[I 2022-06-11 20:56:03,466] Trial 15 finished with value: 0.19509777178646526 and parameters: {'learning_rate': 0.024552396238104734, 'n_estimators': 997, 'min_samples_split': 3, 'min_samples_leaf': 5, 'max_depth': 3}. Best is trial 15 with value: 0.19509777178646526.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:04,065] Trial 16 finished with value: 0.19782340637944174 and parameters: {'learning_rate': 0.031973354037865456, 'n_estimators': 997, 'min_samples_split': 2, 'min_samples_leaf': 5, 'max_depth': 3}. Best is trial 15 with value: 0.19509777178646526.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for exa

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:10,923] Trial 31 finished with value: 0.19767283779005929 and parameters: {'learning_rate': 0.022911199580782176, 'n_estimators': 836, 'min_samples_split': 8, 'min_samples_leaf': 7, 'max_depth': 3}. Best is trial 20 with value: 0.19242156660914989.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:11,618] Trial 32 finished with value: 0.2076181310364612 and parameters: {'learning_rate': 0.02689259657889751, 'n_estimators': 957, 'min_samples_split': 9, 'min_samples_leaf': 6, 'max_depth': 4}. Best

[I 2022-06-11 20:56:18,976] Trial 46 finished with value: 0.16650189538429794 and parameters: {'learning_rate': 0.0077821617877010035, 'n_estimators': 956, 'min_samples_split': 9, 'min_samples_leaf': 1, 'max_depth': 4}. Best is trial 44 with value: 0.15899948595797098.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:19,898] Trial 47 finished with value: 0.1485935899044296 and parameters: {'learning_rate': 0.007104269897951443, 'n_estimators': 962, 'min_samples_split': 10, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 47 with value: 0.1485935899044296.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for exa

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:33,329] Trial 62 finished with value: 0.1693610799796773 and parameters: {'learning_rate': 0.005810092048794899, 'n_estimators': 914, 'min_samples_split': 10, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 51 with value: 0.146411140965093.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 20:56:34,205] Trial 63 finished with value: 0.15918130641379047 and parameters: {'learning_rate': 0.006490818945292811, 'n_estimators': 827, 'min_samples_split': 10, 'min_samples_leaf': 2, 'max_depth': 7}. Bes

...

[I 2022-06-11 23:31:20,483] Trial 9936 finished with value: 0.16349734496308554 and parameters: {'learning_rate': 0.08576764152748002, 'n_estimators': 681, 'min_samples_split': 4, 'min_samples_leaf': 1, 'max_depth': 5}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:31:21,485] Trial 9937 finished with value: 0.15238377407227766 and parameters: {'learning_rate': 0.09982797808898274, 'n_estimators': 601, 'min_samples_split': 3, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), f

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:31:37,142] Trial 9952 finished with value: 0.1365156029769028 and parameters: {'learning_rate': 0.09997611006203318, 'n_estimators': 689, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:31:38,283] Trial 9953 finished with value: 0.15617453102279377 and parameters: {'learning_rate': 0.08542679221706868, 'n_estimators': 668, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 7}.

[I 2022-06-11 23:31:53,182] Trial 9967 finished with value: 0.1492031957031772 and parameters: {'learning_rate': 0.09185383286536117, 'n_estimators': 673, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:31:54,271] Trial 9968 finished with value: 0.16174178564190345 and parameters: {'learning_rate': 0.0713705620179755, 'n_estimators': 680, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 5}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:32:10,506] Trial 9983 finished with value: 0.1531393507890466 and parameters: {'learning_rate': 0.09175865087538612, 'n_estimators': 634, 'min_samples_split': 6, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:32:11,696] Trial 9984 finished with value: 0.15552356203799245 and parameters: {'learning_rate': 0.08539369719353221, 'n_estimators': 689, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 6}.

[I 2022-06-11 23:32:27,061] Trial 9998 finished with value: 0.16441635405982935 and parameters: {'learning_rate': 0.09212451273126876, 'n_estimators': 654, 'min_samples_split': 5, 'min_samples_leaf': 2, 'max_depth': 6}. Best is trial 3608 with value: 0.13382672070440027.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-11 23:32:27,989] Trial 9999 finished with value: 0.15734047033119247 and parameters: {'learning_rate': 0.09998546339085443, 'n_estimators': 617, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 5}. Best is trial 3608 with value: 0.13382672070440027.


In [8]:
study.best_trial

FrozenTrial(number=3608, values=[0.13382672070440027], datetime_start=datetime.datetime(2022, 6, 11, 21, 49, 10, 79580), datetime_complete=datetime.datetime(2022, 6, 11, 21, 49, 11, 11668), params={'learning_rate': 0.09909403062976262, 'n_estimators': 690, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 6}, distributions={'learning_rate': LogUniformDistribution(high=0.1, low=0.001), 'n_estimators': IntUniformDistribution(high=1000, low=10, step=1), 'min_samples_split': IntUniformDistribution(high=10, low=2, step=1), 'min_samples_leaf': IntUniformDistribution(high=10, low=1, step=1), 'max_depth': IntUniformDistribution(high=10, low=1, step=1)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=3608, state=TrialState.COMPLETE, value=None)

In [9]:
study.best_trial.params

{'learning_rate': 0.09909403062976262,
 'n_estimators': 690,
 'min_samples_split': 5,
 'min_samples_leaf': 1,
 'max_depth': 6}

In [10]:
params = study.best_trial.params
lr = params['learning_rate']
n_estimators = params['n_estimators']
min_samples_split = params['min_samples_split']
min_samples_leaf = params['min_samples_leaf']
max_depth = params['max_depth']

gbr = GradientBoostingRegressor(
    learning_rate=lr, 
    n_estimators=n_estimators, 
    min_samples_split=min_samples_split,
    min_samples_leaf=min_samples_leaf,
    max_depth=max_depth)
gbr.fit(x_train_std, y_train)

pred_gbr = gbr.predict(x_test_std)
r2_gbr = r2_score(y_test, pred_gbr)
mae_gbr = mean_absolute_error(y_test, pred_gbr)

print("R2 : %.3f" % r2_gbr)
print("MAE : %.3f" % mae_gbr)

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


R2 : 0.863
MAE : 2.330
